# Ultimate Fandoms

In [1]:
# Imports for the whole Analysis

# imports
from urllib.request import urlopen
import json
import re
from urllib.parse import quote
import pandas as pd
from pandas.io.json import json_normalize
import collections
import itertools
import networkx as nx
import matplotlib.pyplot as plt
from fa2 import ForceAtlas2
import numpy as np
import datetime
from lxml import html
import glob
import ast # string to dirc
import math # check if float is NaN

In [2]:
# Get wikis/dataset from csv
fullDataSet = pd.read_csv("data/sortedWikiData.csv", sep='\t')

# Drop old index column named "Unnamed: 0"
fullDataSet = fullDataSet.drop(['Unnamed: 0'], axis=1)

In [3]:
# Methode that remove inactive wikis and duplicates
def findActiveWikis(dataSet):
    activeDataSet = pd.DataFrame()
    
    # Remove duplicates
    dataSet = dataSet.drop_duplicates()
    
    # Find stats in dataset
    for wiki in dataSet.T.items():
        wiki = wiki[1]
        stats = wiki['stats']
        
        # Only add wiki to list when at in contains at least 1 active user
        sDirc = ast.literal_eval(stats)
        if int(sDirc['activeUsers'])>1:
            activeDataSet = activeDataSet.append(wiki) 
    
    # Create new index
    activeDataSet = activeDataSet.reset_index(drop=True)
    return activeDataSet

In [4]:
### Filter Wiki Data ###
activeDataSet = findActiveWikis(fullDataSet)

print("%s Wikis before filter, and %s Wikis efter filter.\n%s has been removed" % 
      (len(fullDataSet),len(activeDataSet),len(fullDataSet)-len(activeDataSet)))

# Data memory usage
print(sum(activeDataSet.memory_usage(index=False, deep=True))/1000)

activeDataSet.head()

35039 Wikis before filter, and 5585 Wikis efter filter.
29454 has been removed
7978.467


creation_date                                               desc  \
0  2006-01-10 15:06:36                                                NaN   
1  2006-05-27 12:27:18                                                NaN   
2  2007-11-12 08:47:09  Greek is an ABC comedy series following studen...   
3  2009-05-29 21:43:42                                                NaN   
4  2009-07-18 15:01:24  Here at the OZ TV Wikia community we dedicated...   

                   domain flags  founding_user_id  \
0  broadcasting.wikia.com    []           12423.0   
1         zh.tv.wikia.com    []           23838.0   
2       greektv.wikia.com    []          245831.0   
3      smtvlive.wikia.com    []         1393647.0   
4          oztv.wikia.com    []         1469765.0   

                           headline hub       id  \
0                               NaN  TV    942.0   
1                               NaN  TV   1592.0   
2        Welcome to the Greek Wiki!  TV   4477.0   
3                               NaN  TV  26398.0   
4  Learn more about the Oz TV Wikia  TV  37717.0   

                                               image   lang language  \
0                                                NaN     en       en   
1                                                NaN  zh-tw    zh-tw   
2  https://images.wikia.nocookie.net/__cb20161102...     en       en   
3                                                NaN     en       en   
4  https://images.wikia.nocookie.net/__cb20161102...     en       en   

                         name            original_dimensions  \
0  Radio-TV Broadcast History                            NaN   
1                      中文電視大典                            NaN   
2        Greek TV Series Wiki  {'width': 480, 'height': 320}   
3             SM:tv Live Wiki                            NaN   
4                  Oz TV Wiki  {'width': 500, 'height': 320}   

                                               stats  \
0  {'edits': 24380, 'articles': 4362, 'pages': 56...   
1  {'edits': 18338, 'articles': 977, 'pages': 403...   
2  {'edits': 1687, 'articles': 82, 'pages': 558, ...   
3  {'edits': 794, 'articles': 41, 'pages': 406, '...   
4  {'edits': 7750, 'articles': 370, 'pages': 2124...   

                        title  \
0  Radio-TV Broadcast History   
1                      中文電視大典   
2        Greek TV Series Wiki   
3             SM:tv Live Wiki   
4                  Oz TV Wiki   

                                            topUsers          topic  \
0  [4106832, 27024879, 36887098, 37504326, 268032...      Education   
1  [36879666, 36808293, 36843235, 4784321, 581119...             TV   
2  [27262712, 35817224, 30088906, 37296348, 33484...          Humor   
3  [36603313, 37317816, 32946464, 37031283, 37105...             TV   
4  [32455677, 35064581, 25687838, 1469765, 293452...  Entertainment   

                             url  wam_score  \
0  http://broadcasting.wikia.com     2.4801   
1         http://zh.tv.wikia.com     4.7445   
2       http://greektv.wikia.com     1.0088   
3      http://smtvlive.wikia.com     0.0000   
4          http://oztv.wikia.com     3.7153   

                                            wordmark  
0                                                NaN  
1                                                NaN  
2  https://vignette4.wikia.nocookie.net/greektv/i...  
3  https://images.wikia.com/smtvlive/images/8/89/...  
4  https://images.wikia.com/oztv/images/8/89/Wiki...

In [ ]:
###### Save article ID data in hub-search-articles-hub-date #####
date = datetime.date.today().strftime("%d-%m-%Y")
base_query = "http://www.wikia.com/api/v1/Articles/TopByHub?hub="
ns_all = ['110','1']

for hub in set(activeDataSet["hub"]):
    if str(hub) == 'nan':
            continue
    for ns in ns_all:

        query = base_query+hub+"&namespaces="+ns
        response = urlopen(query)
        wikisource = response.read()
        data = json.loads(wikisource)
        print(hub, ns, '\n',
              len(data['items']),
              len(data['items'][0]['articles']), 
              '\n', query)
        #[print(articles['articles']) for articles in data['items']]
    
        # Save data at data/wikis/top-wikis-date.json
        with open("data/articles/hub-search-articles-"+hub+"-"+date+'-'+ns+".json", 'w') as outfile:
            json.dump(data, outfile)
    

In [ ]:
def searchForArticles(domain, article_id_list):
    article_id_string = '%2C'.join(article_id_list)
    query = domain+"/api/v1/Articles/Details?ids="+article_id_string+"&abstract=500&width=200&height=200"
    response = urlopen(query)
    wikisource = response.read()
    return json.loads(wikisource)

In [ ]:
def searchForArticlesSimple(domain, article_id_list):
    error = 0
    data = []
    for article_id in article_id_list:
        try:
            query = domain+"/api/v1/Articles/AsSimpleJson?id="+str(article_id)
            response = urlopen(query)
            wikisource = response.read()
            data.append(json.loads(wikisource))
        except:
            print(domain, article_id, 'error')
            error +=1
    print(len(data), error)
    return data

In [ ]:
###### Save inital data in top-wikis-date #####
def find_articles(data):
    data = ast.literal_eval(str(data))
    data = data['items']
    for wiki in data:
        wiki_data = wiki['wiki']
        domain = wiki_data['domain']
        name = wiki_data['name']
        
        wiki_id = str(wiki_data['id'])
        articles = []
        article_data = []
            
        for article in wiki['articles']:
            articles.append(str(article['id']))
            
        print(name)
        article_data.append(searchForArticlesSimple(domain, articles))
            #wiki_article_ids = name+' ['+wiki_id+']: '
            
            #sections = article_data['sections']
            #for article in sections:
            #    print(article['title'])
            #    for content in article['content']:
            #        if 'text' in content:
            #            print(content['text'])
            #        else:
            #            print(content)
            #print()
    return article_data

In [ ]:
for dataPath in glob.glob("data/articles/*.json"):
    print('_______________', dataPath)
    with open(dataPath) as f:
        json_file = json.loads(f.read())
    file_name = dataPath.replace('articles/','text/text-')
    #file_name = file_name.replace('.json','.txt')
    with open(file_name, 'w') as outfile:
        json.dump(find_articles(json_file), outfile)

In [ ]:
for dataPath in glob.glob("data/text/*.json"):
    print('_______________', dataPath)
    with open(dataPath) as f:
        json_file = json.loads(f.read())
    for section in json_file:
        for s in section:
            for b in s['sections']:
                print('# # # ', b['title'])
                #print(b['level'])
                for c in b['content']:
                    if c['type'] == 'paragraph':
                        print('', c['text'])
                    elif c['type'] == 'list':
                        [print('-', d['text']) for d in c['elements']]
                        
                    else:
                        print('ERROR?!?!', c)
                        
            print()

In [ ]:
#query = 'http://fallout.wikia.com/d/f?sort=trending'
#response = urlopen(query)
#wikisource = response.read()
#regstring = "http://fallout.wikia.com/d/p/3343172654596187821"
#usernames = re.findall(regstring,str(wikisource))
#wikisource

In [ ]:
#query = 'http://fallout.wikia.com/d/p/3343172654596187821'
#response = urlopen(query)
#wikisource = response.read()
#regstring = "<div class=\"post-content\">(.*?)(<\/div>|<div)"
#usernames = re.findall(regstring,str(wikisource))
#[print(a[0], end='\n\n') for a in usernames]

In [25]:
activeDataSet.head()

creation_date                                               desc  \
0  2006-01-10 15:06:36                                                NaN   
1  2006-05-27 12:27:18                                                NaN   
2  2007-11-12 08:47:09  Greek is an ABC comedy series following studen...   
3  2009-05-29 21:43:42                                                NaN   
4  2009-07-18 15:01:24  Here at the OZ TV Wikia community we dedicated...   

                   domain flags  founding_user_id  \
0  broadcasting.wikia.com    []           12423.0   
1         zh.tv.wikia.com    []           23838.0   
2       greektv.wikia.com    []          245831.0   
3      smtvlive.wikia.com    []         1393647.0   
4          oztv.wikia.com    []         1469765.0   

                           headline hub       id  \
0                               NaN  TV    942.0   
1                               NaN  TV   1592.0   
2        Welcome to the Greek Wiki!  TV   4477.0   
3                               NaN  TV  26398.0   
4  Learn more about the Oz TV Wikia  TV  37717.0   

                                               image   lang   ...     \
0                                                NaN     en   ...      
1                                                NaN  zh-tw   ...      
2  https://images.wikia.nocookie.net/__cb20161102...     en   ...      
3                                                NaN     en   ...      
4  https://images.wikia.nocookie.net/__cb20161102...     en   ...      

                         name            original_dimensions  \
0  Radio-TV Broadcast History                            NaN   
1                      中文電視大典                            NaN   
2        Greek TV Series Wiki  {'width': 480, 'height': 320}   
3             SM:tv Live Wiki                            NaN   
4                  Oz TV Wiki  {'width': 500, 'height': 320}   

                                               stats  \
0  {'edits': 24380, 'articles': 4362, 'pages': 56...   
1  {'edits': 18338, 'articles': 977, 'pages': 403...   
2  {'edits': 1687, 'articles': 82, 'pages': 558, ...   
3  {'edits': 794, 'articles': 41, 'pages': 406, '...   
4  {'edits': 7750, 'articles': 370, 'pages': 2124...   

                        title  \
0  Radio-TV Broadcast History   
1                      中文電視大典   
2        Greek TV Series Wiki   
3             SM:tv Live Wiki   
4                  Oz TV Wiki   

                                            topUsers          topic  \
0  [4106832, 27024879, 36887098, 37504326, 268032...      Education   
1  [36879666, 36808293, 36843235, 4784321, 581119...             TV   
2  [27262712, 35817224, 30088906, 37296348, 33484...          Humor   
3  [36603313, 37317816, 32946464, 37031283, 37105...             TV   
4  [32455677, 35064581, 25687838, 1469765, 293452...  Entertainment   

                             url wam_score  \
0  http://broadcasting.wikia.com    2.4801   
1         http://zh.tv.wikia.com    4.7445   
2       http://greektv.wikia.com    1.0088   
3      http://smtvlive.wikia.com    0.0000   
4          http://oztv.wikia.com    3.7153   

                                            wordmark articles  
0                                                NaN       []  
1                                                NaN       []  
2  https://vignette4.wikia.nocookie.net/greektv/i...       []  
3  https://images.wikia.com/smtvlive/images/8/89/...       []  
4  https://images.wikia.com/oztv/images/8/89/Wiki...       []  

[5 rows x 21 columns]

In [5]:
# https://tea.wikia.com/api.php?action=query&list=wkpoppages
# https://broadcasting.wikia.com/api.php?action=query&list=wkpoppages
print("Start!")
query_extention = "/api.php?action=query&list=wkpoppages"
i = 0
j = 0
l = 0
counter = 0
length = len(activeDataSet)
all_articles = []
for wiki in activeDataSet.T.items():
    wiki = wiki[1]
    domain = wiki['domain']
    wiki_articles =[]
    
    query = "https://"+str(domain)+query_extention
    print(query)
    try:
        response = urlopen(query)
        wikisource = response.read()
        #print(wikisource)
    
        regex_string = "item id=&quot;(.*?)&quot; title=&quot;(.*?)&quot;"
        wiki_articles = re.findall(regex_string,str(wikisource))
        
        if len(wiki_articles) == 0:
            print(wiki_articles)
            l+=1
        else:
            print(wiki_articles)
            j+=1
    except Exception as e:
        print('____________ERROR!!_______________')
        print(str(e)[:100])
        i+=1
    
    all_articles.append(wiki_articles)
    counter+=1
    
    if counter % 500 == 0:
        print()
        print("##################################")
        print(counter, length, len(all_articles))
        print("#################################")
    
    print()

# Result
print("Total found:", j, len(all_articles))
print("Total errors:", i)
print("Total not found:", l)

Start!
https://broadcasting.wikia.com/api.php?action=query&list=wkpoppages
[('4', 'Main_Page'), ('3795', 'Telemundo'), ('3914', 'List_of_ABC_slogans'), ('3195', 'United_States_call_letter_assignments'), ('3800', 'Trinity_Broadcasting_Network'), ('2072', 'List_of_United_States_AM_frequency_allocations'), ('4112', 'Personalities_of_WAGA-TV'), ('3615', 'Home_Shopping_Network'), ('3439', 'American_Broadcasting_Company'), ('3045', 'Chronologies'), ('4129', 'Personalities_of_WXIA-TV'), ('3907', 'List_of_CBS_slogans'), ('3843', 'ION_Television'), ('4839', 'List_of_NBC_slogans'), ('3503', 'Mass_media'), ('3563', 'Disney_Channel'), ('3474', 'Miscellaneous_unorganized_material/WSOC-TV'), ('3782', 'Miscellaneous_unorganized_material/KOTV'), ('3568', 'TBS_(TV_network)'), ('3578', 'Eyewitness_News'), ('3538', 'NBC_Weather_Plus'), ('3576', 'Call_sign'), ('3535', 'CBS'), ('3440', 'NBC'), ('3845', 'Miscellaneous_unorganized_material/KSWO-TV')]

https://zh.tv.wikia.com/api.php?action=query&list=wkpoppa

[('1461', 'Main_Page'), ('2655', 'Soluna'), ('1764', 'Characters'), ('1959', 'Cilin'), ('1766', 'The_Fat_Guy'), ('1811', 'Games'), ('1949', 'Ape-Ball'), ('1900', 'Kill_Bot'), ('2712', 'Soluna_Armaments'), ('1950', 'ZooChomper'), ('1765', 'Zoovac'), ('1877', 'Groups_&amp;amp;_Organizations'), ('1784', 'Ginkus'), ('1821', 'Xaq'), ('3056', 'Skills'), ('1886', 'Inventory_Items'), ('2737', 'Abilities_(Soluna)'), ('2715', 'Soluna_Equipments'), ('1994', 'Umbrian'), ('1982', 'About_Paper_Computer_Games'), ('2089', 'Morlocks'), ('2685', 'White_Magic'), ('2584', 'Elves'), ('2055', 'REGenesis'), ('3051', 'Gear')]

https://tonyhawkgames.fandom.com/api.php?action=query&list=wkpoppages
[('1461', 'Main_Page'), ('1793', 'Tony_Hawk&amp;#039;s_American_Wasteland'), ('1787', 'Tony_Hawk&amp;#039;s_Underground_2'), ('1957', 'Eric_Sparrow'), ('1825', 'Tony_Hawk&amp;#039;s_Underground'), ('1784', 'Tony_Hawk&amp;#039;s_Proving_Ground'), ('2345', 'Nyjah_Huston'), ('1819', 'Tony_Hawk&amp;#039;s_Project_8'), ('1

[('1461', 'The_Independent_Games_Wiki'), ('2461', 'Minecraft'), ('2621', 'Qwop'), ('2635', 'Super_Meat_Boy'), ('2037', 'List_of_Indie_Game_Developers'), ('2076', 'Anna_Anthropy'), ('2025', 'Super_Joe'), ('2325', 'Games'), ('2171', 'Arthur_Lee'), ('2109', 'Derek_Yu'), ('2065', 'Paul_Eres'), ('2057', 'Phil_Fish'), ('2108', 'Terry_Cavanagh'), ('2133', 'Stephen_Lavelle'), ('3985', 'Daphny_David'), ('2202', 'Spelunky'), ('3610', 'Mat_Dickie'), ('2110', 'Jonatan_S\\xc3\\xb6derstr\\xc3\\xb6m'), ('2443', 'Developers'), ('2042', 'Game_making_tools'), ('2524', 'List_of_games_often_called_art_games'), ('2999', 'Action_52_OWNS'), ('2212', 'Benjamin_Braden'), ('2230', 'Markus_Persson'), ('2029', 'Cave_Story')]

https://gsorby.wikia.com/api.php?action=query&list=wkpoppages
[('1461', 'Main_Page'), ('2197', 'Template_namespace_templates'), ('2020', 'Mainpage'), ('2176', 'Hey_You,_Pikachu!'), ('2070', 'Resident_Evil_series'), ('2042', 'Resident_Evil_(video_game)'), ('2036', 'Resident_Evil_2'), ('2032',

[('1461', 'Main_Page'), ('2128', 'Cosmo_and_Wanda'), ('2055', 'Valentine&amp;#039;s_Day'), ('2113', 'Easter'), ('2147', 'Trixie_Tang'), ('2032', 'Here_Comes_Peter_Cottontail'), ('2106', 'Macy&amp;#039;s_4th_of_July_Fireworks_Spectacular'), ('2069', 'Love_Potion_976/J'), ('2087', 'Nickelodeon'), ('2266', 'The_Joke&amp;#039;s_on_Schemer'), ('2033', 'The_Easter_Bunny_is_Comin&amp;#039;_To_Town'), ('2108', 'Macy&amp;#039;s_Thanksgiving_Day_Parade'), ('2163', 'Edward&amp;#039;s_ghost_engine'), ('2056', 'Love_Struck!'), ('2093', 'A_DuckTales_Valentine'), ('2190', 'Independence_Day'), ('2119', 'Thanksgiving'), ('2223', 'Mr._Conductor&amp;#039;s_Fourth_of_July'), ('2207', 'Episodes'), ('2170', '&amp;#039;Arry_and_Bert'), ('2075', 'Rudolph&amp;#039;s_Shiny_New_Year'), ('2083', 'New_Year&amp;#039;s'), ('2061', 'Yogi_the_Easter_Bear'), ('2036', 'A_Charlie_Brown_Thanksgiving'), ('2221', 'He_Loves_Me,_He_Loves_Me_Not')]

https://nakedbrothersband.wikia.com/api.php?action=query&list=wkpoppages
[('14

hostname 'fi.ww2books.wikia.com' doesn't match either of '*.wikia-services.com', '*.fandom-dev.pl', 

https://garthnix.wikia.com/api.php?action=query&list=wkpoppages
[('1461', 'Main_Page'), ('1881', 'Nine_Bright_Shiners'), ('1880', 'Astarael'), ('1906', 'Yrael'), ('1876', 'Kibeth'), ('1879', 'Saraneth'), ('1885', 'Mister_Monday'), ('1886', 'Stilken'), ('1983', 'Old_Kingdom_Series'), ('1883', 'Bells'), ('1979', 'Orannis'), ('1878', 'Belgaer'), ('1890', 'The_Keys_To_The_Kingdom'), ('1875', 'Mosrael'), ('1874', 'Ranna'), ('1943', 'Lirael_(Character)'), ('1954', 'Sabriel_(Character)'), ('1873', 'Necromantic_Bells'), ('1877', 'Dyrim'), ('1905', 'The_House'), ('1903', 'Superior_Saturday'), ('1870', 'Sabriel_(book)'), ('1900', 'The_Keys'), ('1904', 'The_Keys_To_The_Kingdom'), ('1950', 'King_Touchstone')]

https://childrensbooks.wikia.com/api.php?action=query&list=wkpoppages
[('1461', 'Children&amp;#039;s_Books_Wiki'), ('2034', 'Charlie_and_the_Chocolate_Factory'), ('2065', 'The_Lord_of_the_Ri

...

[]

https://pl.undertalefandomek.wikia.com/api.php?action=query&list=wkpoppages
____________ERROR!!_______________
hostname 'pl.undertalefandomek.wikia.com' doesn't match either of '*.wikia-services.com', '*.fandom-

https://pt-br.undertale-wiki-brasil.wikia.com/api.php?action=query&list=wkpoppages
____________ERROR!!_______________
hostname 'pt-br.undertale-wiki-brasil.wikia.com' doesn't match either of '*.wikia-services.com', '*.

https://usarblx.wikia.com/api.php?action=query&list=wkpoppages
[]

https://united-states-of-america1.fandom.com/api.php?action=query&list=wkpoppages
[]

https://unstoppable2018.wikia.com/api.php?action=query&list=wkpoppages
[]

https://ms.upinipin.wikia.com/api.php?action=query&list=wkpoppages
____________ERROR!!_______________
hostname 'ms.upinipin.wikia.com' doesn't match either of '*.wikia-services.com', '*.fandom-dev.pl', 

https://victoriassecret.wikia.com/api.php?action=query&list=wkpoppages
[]

https://victoria.wikia.com/api.php?action=query&list=wkp

[]

https://warof1812.wikia.com/api.php?action=query&list=wkpoppages
[]

https://young-shedon.wikia.com/api.php?action=query&list=wkpoppages
[]

https://isu.wikia.com/api.php?action=query&list=wkpoppages
[('1461', 'Ys_Wiki'), ('2054', 'Ys_(series)'), ('2048', 'Ys_Origin'), ('2040', 'Ys_I:_Ancient_Ys_Vanished_~_Omen'), ('2076', 'Ys_VI:_The_Ark_of_Napishtim'), ('2043', 'Ys:_The_Oath_in_Felghana'), ('2081', 'Ys_VI:_The_Ark_of_Napishtim/Characters'), ('2062', 'Adol_Christin'), ('2041', 'Ys_II:_Ancient_Ys_Vanished_\\xe2\\x80\\x93_The_Final_Chapter'), ('2065', 'Ellefale'), ('2093', 'Ys_Legacy'), ('2084', 'Olha'), ('2088', 'Geis'), ('2087', 'Ys_VI:_The_Ark_of_Napishtim/Equipment_&amp;amp;_Items'), ('2058', 'Ys_Seven'), ('2045', 'Ys_IV:_The_Dawn_of_Ys'), ('2042', 'Ys_III:_Wanderers_from_Ys'), ('2090', 'Master-system-ys-the-vanished-omens-box-front.jpg')]

https://pt-br.yugioh.wikia.com/api.php?action=query&list=wkpoppages
____________ERROR!!_______________
hostname 'pt-br.yugioh.wikia.com' doe

[('9615', 'Niklaus_Mikaelson'), ('2039', 'Damon_Salvatore'), ('6291', 'Elijah_Mikaelson'), ('27895', 'Season_Three'), ('40515', 'Rebekah_Mikaelson'), ('2046', 'Stefan_Salvatore'), ('163353', 'The_Departed'), ('2043', 'Caroline_Forbes'), ('74979', 'Kol_Mikaelson'), ('2042', 'Bonnie_Bennett'), ('2390', 'Alaric_Saltzman'), ('2044', 'Tyler_Lockwood'), ('9613', 'Original_Vampire'), ('214896', 'Season_Four'), ('2037', 'Jeremy_Gilbert'), ('4371', 'Elena_and_Damon'), ('90328', 'Klaus_and_Caroline'), ('42010', 'Mikael'), ('142418', 'Heart_of_Darkness'), ('142419', 'Do_Not_Go_Gentle'), ('10476', 'Doppelg\\xc3\\xa4nger'), ('73354', 'Bringing_Out_The_Dead'), ('76926', 'Dangerous_Liaisons'), ('2038', 'Vampire_Diaries_Characters'), ('166175', 'Before_Sunset')]

https://muppet.wikia.com/api.php?action=query&list=wkpoppages
[('4', 'Muppet_Wiki'), ('28859', 'Sesame_Street_Episode_Guide'), ('39', 'Sesame_Street_Characters'), ('98004', 'The_Muppets_Characters'), ('101', 'Muppet_Characters'), ('267', 'Ses

[('1461', 'Wikia'), ('3867', 'Video_Games'), ('3876', 'Entertainment'), ('3875', 'Lifestyle'), ('2043', 'Terms_of_Use'), ('2026', 'About_Us'), ('2060', 'Careers'), ('2067', 'Advertising'), ('2070', 'Privacy_Policy'), ('2672', 'Anime'), ('2414', 'About'), ('2294', 'About_Wikia'), ('4679', 'Entertainment/Avengers_Battle_Royale'), ('2045', 'Press'), ('5186', 'Entertainment/TV_Schedule'), ('2069', 'Licensing'), ('2071', 'Community_Creation_Policy'), ('3085', 'Go'), ('2623', 'Advertising_Examples'), ('2622', 'Our_Audience'), ('2609', 'Our_Clients'), ('4089', 'Wagnike2/Best_Video_Games_of_Spring_2012'), ('3462', 'Wikia_Begins_Next_Growth_Phase_With_Two_Key_Executive_Hires'), ('2608', 'Press_Room'), ('2642', 'Explore_Wikia')]

https://ru.dont-starve.wikia.com/api.php?action=query&list=wkpoppages
____________ERROR!!_______________
hostname 'ru.dont-starve.wikia.com' doesn't match either of '*.wikia-services.com', '*.fandom-dev.pl

https://house-of-cards.wikia.com/api.php?action=query&list=wkpo

[]

https://wiggles.wikia.com/api.php?action=query&list=wkpoppages
[('1816', 'The_Wiggles'), ('1920', 'Wiggles_videos'), ('1964', 'Wiggles_songs'), ('1819', 'The_Wiggles_Movie'), ('1888', 'The_Wiggly_Big_Show'), ('6867', 'Galleries'), ('1880', 'Toot_Toot!_(video)'), ('1809', 'Dorothy_the_Dinosaur'), ('7460', 'Episode_Galleries'), ('1894', 'Hoop-Dee-Doo_It&amp;#039;s_a_Wiggly_Party_(video)'), ('1871', 'Wiggledance!'), ('1822', 'The_Wiggles_(TV_Series_2)'), ('1893', 'Wiggly,_Wiggly_Christmas_(1997_video)'), ('1904', 'It&amp;#039;s_a_Wiggly_Wiggly_World!_(video)'), ('1935', 'Wiggle_Time!_(1998_video)'), ('1946', 'Yummy_Yummy_(1994_video)'), ('2412', 'List_of_The_Wiggles_Videos'), ('1821', 'The_Wiggles_(TV_Series_1)'), ('1840', 'Yummy_Yummy_(1998_video)'), ('1815', 'Murray_Cook'), ('7155', 'Surfer_Jeff_(video)'), ('1813', 'Anthony_Field'), ('1834', 'Jeff_Fatt'), ('2142', 'Yule_Be_Wiggling_(video)'), ('1934', 'Wiggle_Time!')]

https://nanatsu-no-taizai.fandom.com/api.php?action=query&list=w

In [8]:
l+i+j

5585

In [6]:
activeDataSet["articles"] = all_articles

In [7]:
for wiki in activeDataSet.T.items():
    wiki = wiki[1]
    articles = wiki['articles']
    print(articles)

[('4', 'Main_Page'), ('3795', 'Telemundo'), ('3914', 'List_of_ABC_slogans'), ('3195', 'United_States_call_letter_assignments'), ('3800', 'Trinity_Broadcasting_Network'), ('2072', 'List_of_United_States_AM_frequency_allocations'), ('4112', 'Personalities_of_WAGA-TV'), ('3615', 'Home_Shopping_Network'), ('3439', 'American_Broadcasting_Company'), ('3045', 'Chronologies'), ('4129', 'Personalities_of_WXIA-TV'), ('3907', 'List_of_CBS_slogans'), ('3843', 'ION_Television'), ('4839', 'List_of_NBC_slogans'), ('3503', 'Mass_media'), ('3563', 'Disney_Channel'), ('3474', 'Miscellaneous_unorganized_material/WSOC-TV'), ('3782', 'Miscellaneous_unorganized_material/KOTV'), ('3568', 'TBS_(TV_network)'), ('3578', 'Eyewitness_News'), ('3538', 'NBC_Weather_Plus'), ('3576', 'Call_sign'), ('3535', 'CBS'), ('3440', 'NBC'), ('3845', 'Miscellaneous_unorganized_material/KSWO-TV')]
[]
[('1461', 'Main_Page'), ('1801', 'Rusty_Cartwright'), ('1814', 'Cappie'), ('1800', 'Casey_Cartwright'), ('1829', 'Calvin_Owens'), 

[('2025', 'Arcuz'), ('2077', 'Arcuz_2'), ('2014', 'Achievement_Unlocked_9999'), ('2010', 'Sonny'), ('2035', 'Sonny_(Character)'), ('1821', 'Templates'), ('2105', 'Colony'), ('2043', 'Achievment_Unlocked_2'), ('2031', 'Map.png'), ('2030', 'Arcuz_quest.jpg'), ('2061', 'John'), ('2023', 'History'), ('2110', 'Strike_Force_Heroes'), ('2096', 'Crush_the_castle_2'), ('2111', 'Sinjid_Shadow_of_the_Warrior'), ('2046', 'Elephant_Day'), ('2011', 'Sonny'), ('1526', 'Community_Portal'), ('2113', 'Sinjid_Battle_Arena'), ('2060', 'Elephant'), ('2108', 'Dark123456789'), ('2022', 'History_of_Armor_Games'), ('2065', 'Corporation_Incorporated'), ('1975', 'Weeljack'), ('2024', 'Site_Staff')]
[('1461', 'Card_Game_Wiki'), ('2044', 'Face_cards'), ('2032', 'Spades'), ('2033', 'Anglo-American_deck'), ('2020', '300px-French_suits.svg.png'), ('2029', '21_Blackjack'), ('2039', 'Standard_bridge_ordering'), ('1673', 'Welcome'), ('2038', 'Hearts'), ('2050', 'Ace'), ('2051', 'Joker'), ('2040', 'Diamonds'), ('2042', '

[('3', 'Main_Page'), ('146', 'Holy_Roman_Empire'), ('127', 'History_of_globalization'), ('58', 'Timeline_of_History'), ('2338', 'Roman_Republic'), ('20', 'Famous_Events'), ('2437', 'Martin_Luther'), ('2301', 'Allemanni'), ('3706', 'Pan-Arabism'), ('1951', 'Beginning_of_Christianity'), ('119', 'Roman_Empire'), ('2400', 'American_Old_West'), ('74', 'Sumerians'), ('52', 'History_by_Polities'), ('2591', 'House_of_Isenburg'), ('4', 'Famous_People'), ('54', 'World_War_II'), ('2290', 'Germanic_tribes'), ('111', 'List_of_Imperial_Estates_of_the_Holy_Roman_Empire'), ('2051', 'Swabian_Circle'), ('105', 'Early_Egypt'), ('106', 'List_of_Rulers_of_Germany'), ('1648', 'Charles_I_of_Austria'), ('2052', 'Upper_Rhenish_Circle'), ('2826', 'Electorate_of_the_Palatinate')]
[('16', 'Disney_characters'), ('2587', 'Disney_Princess'), ('2105', 'Villains'), ('2540', 'Characters'), ('3959', 'Cinderella_(character)'), ('188', 'Aladdin_(character)'), ('17896', 'Flynn_Rider'), ('40407', 'Tangled_Ever_After'), ('42

[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[('1461', 'XxxHOLiC_Wiki'), ('2073', 'Y\\xc5\\xabko_Ichihara'), ('2093', 'Kimihiro_Watanuki'), ('2072', 'Shizuka_Doumeki'), ('2031', 'Characters'), ('2066', 'Himawari_Kunogi'), ('2032', 'Kohane_Tsuyuri'), ('2045', 'Maru_and_Moro'), ('2343', 'List_of_xxxHolic_episodes'), ('2493', 'Clow_Reed'), ('2820', 'XxxHolic_Protagonists'), ('2202', 'Zashiki_Warashi'), ('2102', 'Mokona_Modoki'), ('2105', 'Tsubasa_Li'), ('2203', 'Ame_Warashi'), ('2205', 'Haruka_Domeki'), ('2153', 'Sakura_Li'), ('2149', 'XxxHolic_Characters'), ('2150', 'Syaoran_Li'), ('2109', 'Princess_Tsubasa'), ('2065', 'XxxHOLiC'), ('2829', 'XxxHolic_Other_Characters'), ('2204', 'Kudakitsune'), ('2323', 'XxxHOLIC\\xe2\\x99\\xa6Rou_OAD'), ('3128', 'Chapter

[]
[('1461', 'Pitfall_Wiki'), ('1825', 'Pitfall_Wiki'), ('1523', 'Sannse'), ('1516', 'Policy')]
[]
[]
[]
[('162', 'Characters'), ('4', 'White_Bomberman'), ('736', 'Bomberman_Games'), ('34', 'Bomberman_64'), ('223', 'Pretty_Bomber'), ('155', 'Bagura'), ('236', 'Black_Bomberman'), ('14', 'Bomberman_64:_The_Second_Attack!'), ('237', 'Villains'), ('11', 'Bomberman_Act:Zero'), ('1823', 'Heroes'), ('146', 'Astral_Knights'), ('228', 'Bomberman_Jetters_(anime)'), ('251', 'Pommy'), ('334', 'Altair'), ('198', 'Regulus'), ('306', 'Sirius'), ('2777', 'Nintendo_64'), ('363', 'Super_Bomberman_3'), ('96', 'Bomberman_Hero'), ('458', 'Max'), ('238', 'Bosses'), ('158', 'Five_Dastardly_Bombers'), ('79', 'Super_Bomberman_4'), ('82', 'Bomberman_Generation')]
[('1512', 'Atheist_vs_Agnostic'), ('2', 'Main_Page'), ('1624', 'How_many_gods?'), ('1756', 'Christian_morality'), ('1693', 'Hell'), ('1757', 'Noah&amp;#039;s_flood'), ('1510', 'Atheist_Politics'), ('1871', 'American_Atheism_is_rising_and_Christians_don

[('1461', 'Main_Page'), ('1806', 'The_Dead_Zone_(TV_series)'), ('1800', 'Greg_Stillson'), ('1801', 'Johnny_Smith'), ('1804', 'The_Dead_Zone_(film)'), ('1802', 'The_Dead_Zone_(novel)'), ('1818', 'Walt_Bannerman'), ('1501', 'About'), ('1807', 'List_of_The_Dead_Zone_episodes'), ('1798', 'Malcolm_Janus'), ('1829', 'Sean_Patrick_Flanery'), ('1795', 'Science_of_The_Dead_Zone'), ('1816', 'Spencer_Achtymichuk'), ('1524', 'Current_events'), ('1809', 'Anthony_Michael_Hall'), ('1817', 'Connor_Price'), ('1803', 'Psychometry'), ('1810', 'John_L._Adams'), ('1526', 'Community_Portal'), ('1812', 'Stephen_King'), ('1808', 'List_of_The_Dead_Zone_episodes'), ('1792', 'Jaster'), ('1674', 'Welcome'), ('1462', 'Index'), ('1799', 'Malcolm_Janus')]
[('1461', 'The_Culture_Wiki'), ('1790', 'The_Culture'), ('1792', 'Idiran-Culture_War'), ('1955', 'Olmedreca'), ('1844', 'Bora_Horza_Gobuchul_(Mind)'), ('1897', 'The_Culture_Universe'), ('1839', 'Bora_Horza_Gobuchul_(Changer)'), ('2109', 'Idiran'), ('1943', 'Systems

[]
[]
[]
[]
[]
[]
[('1461', '101_Dalmatians_Wiki'), ('2040', 'Lucky'), ('2041', 'Rolly'), ('2038', 'Cadpig'), ('2060', 'Two-Tone'), ('2025', '101_Dalmatians:_The_Series'), ('2059', 'List_of_101_Dalmatians:_The_Puppies'), ('2073', 'Perdita'), ('2112', 'Wizzer'), ('2072', 'Pongo'), ('2074', 'Patch'), ('2142', 'List_of_101_Dalmatians:_The_Series_Episodes'), ('2026', 'One_Hundred_and_One_Dalmatians'), ('2102', 'Dipstick'), ('2231', 'Characters'), ('2104', 'Jewel'), ('2107', 'Rebecca'), ('2035', 'Canon_characters'), ('2028', '101_Dalmatians_(1996_film)'), ('2061', 'Penny'), ('2066', 'Cruella_de_Vil'), ('2030', '102_Dalmatians'), ('2037', 'Spot'), ('2029', '101_Dalmatians_II:_Patch&amp;#039;s_London_Adventure'), ('2182', 'Fluffy')]
[]
[]
[('1461', 'Tenchi_Muyo_Wiki'), ('1883', 'Ryoko_Hakubi'), ('1893', 'Washu_Hakubi'), ('1906', 'Tenchi_Muyo!_Ryo-Ohki'), ('1889', 'Sasami'), ('2124', 'Characters'), ('1911', 'Ayeka'), ('1890', 'Mihoshi'), ('2002', 'Kenshi_Masaki'), ('1917', 'Ryo-Ohki'), ('1910'

[]
[]
[]
[]
[]
[]
[]
[]
[('1461', 'So_You_Think_You_Can_Dance_Wiki'), ('2366', 'Alex_Wong'), ('2256', 'Kathryn_McCormick'), ('2257', 'Lauren_Gottlieb'), ('2373', 'Lauren_Froderman'), ('2372', 'Kent_Boyd'), ('2255', 'Dominic_Sandoval'), ('2635', 'Will_Thomas'), ('2375', 'Robert_Roldan'), ('2632', 'Cole_Horibe'), ('2260', 'Pasha_Kovalev'), ('2309', 'Travis_Wall'), ('2251', 'Allison_Holker'), ('2252', 'Anya_Garnis'), ('2032', 'Season_5'), ('2077', 'Phillip_Chbeeb'), ('2254', 'Courtney_Galiano'), ('2382', 'Season_7'), ('2258', 'Mark_Kanemura'), ('2288', 'Debbie_Allen'), ('2147', 'Nigel_Lythgoe'), ('2627', 'Eliana_Girard'), ('2644', 'Tiffany_Maher'), ('2369', 'Billy_Bell'), ('2368', 'Ashley_Galvan')]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[('1461', 'Main_Page'), ('1782', 'Mark_Hoffman'), ('1774', 'Lawrence_Gordon'), ('1731', 'Amanda_Young'), ('1846', 'Reverse_Beartrap'), ('1732', 'Adam_Stanheight'), ('1851', 'Jill_Tuck'), ('1771', 'Characters'), ('1791', 'Eric_Matthews'), ('1858', 'An

In [9]:
# Save Collected data
date = datetime.date.today().strftime("%d-%m-%Y")
activeDataSet.to_csv("data/activeDataSetWithArticles-"+date+".csv", sep='\t')

In [42]:
def searchArticlesSimple(domain, article_list):
    error = 0
    data = []
    print(len(article_list), end=', ')
    for article in article_list:
        try:
            query = "https://"+domain+"/api/v1/Articles/AsSimpleJson?id="+str(article[0])
            response = urlopen(query)
            wikisource = response.read()
            data.append(json.loads(wikisource))
        except Exception as e:
            #print(domain, article[0], 'error')
            print(str(e)[:100])
            error +=1
    print(len(data), error, str(data)[:500])
    return data

In [45]:
article_data = {}
for wiki in activeDataSet.T.items():
    wiki = wiki[1]
    hub = wiki['hub']
    print(wiki['title'])
    if hub not in article_data:
        article_data[hub] = []
    article_data[hub].append((wiki['title'], searchArticlesSimple(wiki['domain'], wiki['articles'])))  
    print()

Radio-TV Broadcast History
25, 25 0 [{'sections': [{'title': 'Main Page', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Hello! You have entered the  Wiki, begun in January 2006. Currently (as of December 11, 2018) there are 4,362 articles that have been created for this Wiki.'}, {'type': 'paragraph', 'text': 'The intent of the founder of this Wiki was not so much to discuss program content (though as people become active here, since Wikis tend to be pretty anarchic, they may choose to put in articles relating to program c

中文電視大典
0, 0 0 []

Greek TV Series Wiki
25, 25 0 [{'sections': [{'title': 'Main Page', 'level': 1, 'content': [], 'images': []}]}, {'sections': [{'title': 'Rusty Cartwright', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Rusty Cartwright aka "Spitter" is the lead male protagonist of the series. He is the younger brother of Casey Cartwright. After being accepted into Cyprus-Rhodes University, Rusty decides that he no longer wants to be the stereotypic

25, 25 0 [{'sections': [{'title': 'Arcuz', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Website: http://www.armorgames.com'}, {'type': 'paragraph', 'text': 'Official site: Funnault.com'}, {'type': 'paragraph', 'text': 'Arcuz is a RPG game where you, the hero, saves Arcuz Village from a mysterious disaster relating to the disappearence of the landlord that owns the land. You must engage in quests to find out about disappearing villagers and the monsters outside of the village.'}, {'type': 'parag

Card Game Wiki
25, 25 0 [{'sections': [{'title': 'Card Game Wiki', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Card Game Wiki is a collaborative wiki website about card games. You can read up on how to play classic card games, recommend favourites, and add your own invented games to it. This wiki is only for card games that can be played with one or more standard Anglo-American playing card decks or a subset thereof.   Start of left-column - title, contents, help - dynamic 

25, 25 0 [{'sections': [{'title': 'Defias Brotherhood EU Wiki', 'level': 1, 'content': [], 'images': []}]}, {'sections': [{'title': 'Alliance Characters', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'This category is for alliance characters articles and categories on the Defias Brotherhood realm.'}], 'images': []}]}, {'sections': [{'title': 'Alliance Guilds', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'This category is for alliance guilds articles and categories on the Defias Brother

Black Blood Brothers Wiki
25, 25 0 [{'sections': [{'title': 'Jiro Mochizuki', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Jiro Mochizuki (望月 ジロー, Mochizuki Jirō) is the main character of Black Blood Brothers. He is an Old Blood vampire that sided with the humans to fight against the Kowloon children during the Kowloon Shock.'}], 'images': []}, {'title': 'Appearance', 'level': 2, 'content': [{'type': 'paragraph', 'text': 'Jiro is a very handsome young man with long back-leng

17, 17 0 [{'sections': [{'title': 'Junie B. Jones Wiki', 'level': 1, 'content': [], 'images': []}, {'title': 'Welcome To The Junie B. Jones Wiki!', 'level': 2, 'content': [{'type': 'paragraph', 'text': 'This is a place to learn about Junie B  and her friends, (and her enemies) and the books.\xa0'}, {'type': 'paragraph', 'text': 'Junie B. Jones is a children\'s book series written by Barbara Park and illustrated by Denise Brunkus. Published by Random House from 1992-2013, the stories begin with Junie B. J

Tales of The Frog Princess Books Wiki
0, 0 0 []

Michael Vey Books Series Wiki
0, 0 0 []

Living Books Wiki
0, 0 0 []

Comic books in the media Wiki
0, 0 0 []

Canadian Indie Comic Books Wiki
0, 0 0 []

Sheyffer's Book Planning Wiki
0, 0 0 []

Dreadful Books Wiki
0, 0 0 []

12 Books of Caleris Wiki
0, 0 0 []

Music Hub
25, 25 0 [{'sections': [{'title': 'Music Wiki/old', 'level': 1, 'content': [], 'images': []}]}, {'sections': [{'title': 'Erection', 'level': 1, 'content': [{'type': 'pa

25, 25 0 [{'sections': [{'title': 'UK Comics Wiki', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'This is a Wiki dedicated to British comics. So far it has 1,553 articles (recent changes).'}], 'images': [{'src': 'https://vignette.wikia.nocookie.net/ukcomics/images/b/b0/Desperatedan1946.jpg/revision/latest/scale-to-width-down/269?cb=20100920095558', 'caption': ''}]}, {'title': 'A few guidelines...', 'level': 2, 'content': [{'type': 'list', 'elements': [{'text': 'Most wikis insist on a formal writ

Archie Comics Wiki
25, 25 0 [{'sections': [{'title': 'Archie Comics Wiki', 'level': 1, 'content': [], 'images': []}, {'title': 'Archie wikis', 'level': 2, 'content': [{'type': 'list', 'elements': [{'text': 'Riverdale (CW show)', 'elements': []}, {'text': 'Sabrina TheTeenage Witch (1996 show)', 'elements': []}, {'text': 'Sabrina: The Animated Series', 'elements': []}, {'text': 'Secrets of a Teenage Witch (2013 Animated show)', 'elements': []}]}], 'images': []}]}, {'sections': [{'title'

...

25, 25 0 [{'sections': [{'title': 'Moshlings', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Category for Moshlings, and everyone related to them.'}], 'images': []}]}, {'sections': [{'title': 'Moshi Monsters Wiki', 'level': 1, 'content': [], 'images': []}]}, {'sections': [{'title': 'Dustbin Beaver', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Dustbin Beaver the Moptop Tweenybop is a former\xa0Moshling\xa0in\xa0Moshi Monsters.'}, {'type': 'paragraph', 'text': "Until November 21, 2013 y

Monsters, Inc. Wiki
0, 0 0 []

Moomoo.io Wiki
0, 0 0 []

MooMoo Wiki
0, 0 0 []

Motherload Wiki
25, 25 0 [{'sections': [{'title': 'Motherload Wiki', 'level': 1, 'content': [], 'images': [{'src': 'https://vignette.wikia.nocookie.net/motherload1/images/8/8f/Wiki-Preview.png/revision/latest?cb=20091116072214'}]}, {'title': 'Motherload is a delightful game similar to the arcade classic "Dig Dug". Some of the early-game materials that you can obtain for sale are Ironium, Bronzium, Silveriu

25, 25 0 [{'sections': [{'title': 'So Random', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'So Random! is an American Disney Channel sketch series that premiered on June 5, 2011. It was announced as an independent series after Demi Lovato left the parent series, Sonny with a Chance, to focus on other endeavors. The series stars the other actors of Sonny with a Chance: Tiffany Thornton, Sterling Knight, Brandon Mychal Smith, Doug Brochu and Allisyn Ashley Arm as well as other featured actors tha

Random Wiki
0, 0 0 []

The Random Wiki
0, 0 0 []

Random Wiki
0, 0 0 []

The Random Wiki
0, 0 0 []

Rayman Wiki
0, 0 0 []

Rayman Wiki
0, 0 0 []

Wireless Wiki
0, 0 0 []

Unreal Wiki
25, 25 0 [{'sections': [{'title': 'Unreal Main Page', 'level': 1, 'content': [], 'images': []}]}, {'sections': [{'title': 'Unreal Tournament 3', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Unreal Tournament 3 is the eighth entry in the Unreal series and the fourth entry in the Unreal Tournament

25, 25 0 [{'sections': [{'title': 'The Flash Wiki', 'level': 1, 'content': [], 'images': []}]}, {'sections': [{'title': 'The Flash (Barry Allen)', 'level': 1, 'content': [], 'images': []}, {'title': 'History', 'level': 2, 'content': [], 'images': []}, {'title': 'Origin', 'level': 3, 'content': [{'type': 'paragraph', 'text': 'Barry Allen Born Bartholomew Henry Allen also known as The Flash is a Metahuman Speedsters and The Fastest Man Alive or The Scarlet Speedster who gained his Powers from The Speed For

The Flash Wiki
0, 0 0 []

The Flash Wiki
0, 0 0 []

The Flash Wiki
0, 0 0 []

Wiki The Flash
0, 0 0 []

The Flash Wiki
0, 0 0 []

The Fosters Wiki
0, 0 0 []

The Good Place Wiki
0, 0 0 []

The Human Centipede Wiki
10, 10 0 [{'sections': [{'title': 'The Human Centipede Wiki', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Welcome to the The Human Centipede Wiki'}, {'type': 'paragraph', 'text': "The Human Centipede is a series of body horror films created by Dutch filmmaker Tom 

25, 25 0 [{'sections': [{'title': 'Red Dead Wiki', 'level': 1, 'content': [], 'images': []}]}, {'sections': [{'title': 'Weapons in Redemption', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'There are a variety of weapons featured in Red Dead Redemption. They are essential to survival, as well as an integral part of everyday life in the American West. The player is able to use a range of weapons ranging from Civil War era manually operated weapons all the way to the cutting edge, semi-automatic w

Marvel Database
25, 25 0 [{'sections': [{'title': 'Characters', 'level': 1, 'content': [], 'images': [{'src': 'https://vignette.wikia.nocookie.net/marveldatabase/images/e/e1/The_Marvel_Universe.png/revision/latest/scale-to-width-down/630?cb=20110513164401'}]}]}, {'sections': [{'title': 'Peter Parker (Earth-616)', 'level': 1, 'content': [], 'images': []}, {'title': 'History', 'level': 2, 'content': [{'type': 'paragraph', 'text': "\xa0 This is an abridged version of Peter Parker's histo

25, 25 0 [{'sections': [{'title': 'Wikia', 'level': 1, 'content': [], 'images': []}]}, {'sections': [{'title': 'Video Games', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'video games'}], 'images': []}]}, {'sections': [{'title': 'Entertainment', 'level': 1, 'content': [{'type': 'paragraph', 'text': '__NORAIL__ __NONAV__ __NOSPOTLIGHTS__'}], 'images': []}]}, {'sections': [{'title': 'Lifestyle', 'level': 1, 'content': [{'type': 'paragraph', 'text': '__NORAIL__ __NONAV__ __NOSPOTLIGHTS__'}], 'image

Don't Starve вики
0, 0 0 []

House of Cards Wiki
0, 0 0 []

Civilization Wiki
25, 25 0 [{'sections': [{'title': 'Civilization V', 'level': 1, 'content': [{'type': 'paragraph', 'text': 'Main page'}], 'images': []}, {'title': 'The Game', 'level': 2, 'content': [{'type': 'paragraph', 'text': "Sid Meier's Civilization V (called Civilization V or Civ5 for short) is a turn-based strategy game released on September 21, 2010. The game's first expansion pack, Gods & Kings, was released on June

In [47]:
print(len(article_data))
for hub, articles in article_data.items():
    print(hub, len(articles))
    file_name = "data/articles/"+str(hub)+"-articles.json"
    with open(file_name, 'w') as outfile:
        json.dump(articles, outfile)
    

9
TV 1111
Games 2355
Movies 420
Lifestyle 678
Books 446
Comics 364
Music 200
Other 10
nan 1
